In [ ]:
# https://www.analyticsvidhya.com/blog/2016/06/quick-guide-build-recommendation-engine-python/
# http://surpriselib.com/
# https://gitpitch.com/gitpitch/kitchen-sink/master?grs=github&t=night#/

## [RUN THIS FIRST] Packages used 

In [2]:
import requests
import json
import math
import logging
import scrapy
import re
import pandas as pd
import numpy as np
import cufflinks as cf
import ipywidgets as widgets

from scrapy.crawler import CrawlerProcess 
#from scrapy.selector import HtmlXPathSelector
from bs4 import BeautifulSoup
#from scipy.sparse.linalg import svds
#from surprise import Reader, Dataset, SVD, evaluate, CoClustering
#from sklearn.metrics import mean_squared_error
from collections import Counter

cf.go_offline()
# fake to become a browser
headers = { 'User-Agent': 'Mozilla/5.0 (Windows NT 6.0; WOW64; rv:24.0) Gecko/20100101 Firefox/24.0' }

# Gather Reviews for top restaurants

## First ever scrape: Whole HK region (using Openrice API url)

### Get first 17 pages

In [3]:
# grab the entire list of restuarants for HK on openrice, only focusing on the review links
review_url = []
#category_id = []
#category_name = []
name = []
district = []
district_id = []
#price_UI =[]
#address = []
#latitude = []
#longitude = []
review_count = []
#score_smile = []
#score_cry = []
bookmark_count = []
#score_overall = []

# only do 20 pages of restaurants
for i in range(1,20):
    '''
    aliasUI,Count,Type,ID,Name,Search Key
    香港島||Hong Kong Island||香港岛,8838,district,1999,Hong Kong Island,districtId=1999
    九龍||Kowloon||九龙,12375,district,2999,Kowloon,districtId=2999
    新界||New Territories,10637,district,3999,New Territories,districtId=3999
    離島||Outlying Islands||离岛,958,district,4999,Outlying Islands,districtId=4999
    '''
    # focus on non-"Outlying Islands" restaurants
    #r = requests.get("https://www.openrice.com/api/pois?uiLang=en&uiCity=hongkong&page="+ str(i) +"&&sortBy=Default&districtId=1999&districtId=2999&districtId=3999", headers = headers)
    r = requests.get("https://www.openrice.com/api/pois?uiLang=en&uiCity=hongkong&page="+ str(i) +"&&sortBy=Default&districtId=2008", headers = headers)
    result = json.loads(r.text)
    print(result['page'], result['totalPage'])
    # bail of not restaurants
    result_restaurants = result['searchResult']['paginationResult']['results']
    if len(result_restaurants) == 0:
        break

    # grab info from each restaurant
    for result_restaurant in result_restaurants:
        review_url.append(result_restaurant['reviewUrlUI'])
        name.append(result_restaurant['nameUI'].encode('utf-8'))
        district.append(result_restaurant['district']['name'])
        district_id.append(result_restaurant['district']['districtId'])
        #address.append(result_restaurant['address'])        
        #price_UI.append(result_restaurant['priceUI'])
        #latitude.append(result_restaurant['mapLatitude'])
        #longitude.append(result_restaurant['mapLongitude'])
        review_count.append(result_restaurant['reviewCount'])
        #score_smile.append(result_restaurant['scoreSmile'])
        #score_cry.append(result_restaurant['scoreCry'])
        #score_overall.append(result_restaurant['scoreOverall'])
        bookmark_count.append(result_restaurant['bookmarkedUserCount'])        
        
        '''
        holder_category = []
        holder_name = []
        for k in range(len(result_restaurant['categories'])):
            holder_category.append(result_restaurant['categories'][k]['categoryId'])
            holder_name.append(result_restaurant['categories'][k]['name'])
        category_id.append(holder_category)
        category_name.append(holder_name)
        '''
    print(i)
    i += 1

1 17
1
2 17
2
3 17
3
4 17
4
5 17
5
6 17
6
7 17
7
8 17
8
9 17
9
10 17
10
11 17
11
12 17
12
13 17
13
14 17
14
15 17
15
16 17
16
17 17
17
18 17


In [15]:
i=17
r = requests.get("https://www.openrice.com/api/pois?uiLang=en&uiCity=hongkong&page="+ str(i) +"&&sortBy=Default&districtId=2008", headers = headers)
result = json.loads(r.text)


In [16]:
for x in result.keys(): print(x)

searchResult
title
startAt
rows
totalPage
page
mapSearchUrlUI
listSearchUrlUI
nearBySearchUrlUI
closedPoiCount
baseUrl
mobilePagination
desktopPagination
pageInfo


In [7]:
for x in result['searchResult'].keys(): print(x)

paginationResult
isBookingSR1
offerUrl
viewOfferButtonClickEventUI
isRmsSearch
isGuidedSearch
isOrganicSearch
isMmsSearch
isDedicatedSearch
isDeliverySearch
primaryCriterion
isAllRegionSearchResult
showPartnerWithUs
bannerDisplayFormat
bannerRotationTime
suggestedCoupons
resultInOtherRegions
hasNameSort
filterBarOptions
searchHeader
refineSearchFilter
withOffer
offerFilter
isFilterEnabled
isDeliveryEnabled
banners
adsBanners
shortenUrl
districtSearchEnabled
poiSearchEnabled
hideAndSelectedSearchOptions


In [10]:
for x in result['searchResult']['paginationResult'].keys(): print(x)

closedCount
isBookmarkedResult
isFarThanMaximum
results
count
totalReturnCount


In [14]:
result['searchResult']['paginationResult']

{'closedCount': 0,
 'isBookmarkedResult': False,
 'isFarThanMaximum': False,
 'results': [],
 'count': 2120,
 'totalReturnCount': 250}

In [17]:
result['searchResult']['paginationResult']['count']

2120

In [18]:
result['searchResult']['paginationResult']['totalReturnCount']

250

In [19]:
result['searchResult']['paginationResult']['results']

[{'index': 241,
  'categoriesUI': [{'urlUI': '/en/hongkong/restaurants/cuisine/hong-kong-style',
    'searchKey': 'cuisineId=1004',
    'categoryId': 1004,
    'categoryTypeId': 1,
    'regionId': 0,
    'name': 'Hong Kong Style',
    'callName': 'hong-kong-style',
    'status': 0,
    'searchStart': 0,
    'searchEnd': 0,
    'sortOrder': 0},
   {'urlUI': '/en/hongkong/restaurants/dish/hot-pot',
    'searchKey': 'dishId=1001',
    'categoryId': 1001,
    'categoryTypeId': 2,
    'regionId': 0,
    'name': 'Hot Pot',
    'callName': 'hot-pot',
    'status': 0,
    'searchStart': 0,
    'searchEnd': 0,
    'sortOrder': 0}],
  'isMoreThan2CatUI': True,
  'coupons': [],
  'categories': [{'urlUI': '/en/hongkong/restaurants/cuisine/hong-kong-style',
    'searchKey': 'cuisineId=1004',
    'categoryId': 1004,
    'categoryTypeId': 1,
    'regionId': 0,
    'name': 'Hong Kong Style',
    'callName': 'hong-kong-style',
    'status': 0,
    'searchStart': 0,
    'searchEnd': 0,
    'sortOrder': 

In [22]:
result['searchResult']['paginationResult']['results'][0].keys()

dict_keys(['index', 'categoriesUI', 'isMoreThan2CatUI', 'coupons', 'categories', 'district', 'doorPhoto', 'isBookingSR1', 'bookingMenu', 'distanceUI', 'urlUI', 'urlClickEventUI', 'reviewUrlUI', 'photoUrlUI', 'nameUI', 'addressUI', 'priceUI', 'isMoreSmileUI', 'isMoreCryUI', 'isClosedPoiUI', 'bookmarkedUserUI', 'ribbonUI', 'mobileRibbonUI', 'promotions', 'titleBadgesUI', 'bankPromotionsUI', 'popularDishes', 'rmsPhotos', 'rmsPhotosUI', 'countPoiVotesUI', 'isDedicated', 'chainIdUI', 'isFirstPoiInSameRegion', 'regionName', 'mobileRmsPhotosUI', 'createBookingUrlUI', 'tmBookingWidget', 'redirectQueuingUrlUI', 'hasPoiBizCarouselUI', 'hasPremiumMenu', 'michelinText', 'useExpandLayoutBooking', 'useExpandLayoutOffer', 'useExpandLayoutBookingMenu', 'poiId', 'regionId', 'status', 'distance', 'name', 'nameLangIndex', 'nameOtherLang', 'nameOtherLangIndex', 'address', 'addressLangIndex', 'addressOtherLang', 'addressOtherLangIndex', 'info', 'awardInfo', 'postalCode', 'mapLatitude', 'mapLongitude', 'map

In [24]:
result['searchResult']['paginationResult']['results'][0]['urlUI']

'/en/hongkong/r-yum-hotpot-tsim-sha-tsui-hong-kong-style-chicken-hot-pot-r707888'

In [17]:
d = dict(zip(
        ['Name','Review URL','District','District ID','Review Count','Bookmark Count'],
        [name,review_url,district,district_id,review_count,bookmark_count]
    ))
df = pd.DataFrame.from_dict(d)
df.to_csv('review_url_AT.csv',encoding='utf-8',index=False)

### Setting up review urls for scrapy
- Scrape all reviews from all the urls

In [18]:
df = pd.read_csv('review_url_AT.csv')
review_urls = []

for k in range(len(df['Review Count'])):
    num_of_review_pages = math.ceil(df['Review Count'][k] / 15.0)

    for i in range(1,int(num_of_review_pages)):
        review_urls.append('https://www.openrice.com'+ str(df['Review URL'][k]) + '?page='+ str( i ))

print("There is {} urls to scrape".format(len(review_urls)))

There is 14161 urls to scrape


### Scrapy for all reviews for all the urls

In [20]:
'''
scrapy logging techniques
    https://www.youtube.com/watch?v=5YmyALotdn0

    # import logging
    import logging
    self.log(user)

    # inspect_response()
    import scrapy
scrapy runspider python_script.py
'''

class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('reviewresult_AT.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item


import logging # self.log(thing,logging.WARN)
from scrapy.shell import inspect_response # inspect_response(response, self)
# view(response) within scrapy.shell
#from scrapy.utils.response import open_in_browswer # open_in_browser(response)
            
class ExtractSpider(scrapy.Spider):
    name = "Extract"
    start_urls = review_urls

    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1}, # Used for pipeline 1
        'FEED_FORMAT':'json',                                 # Used for pipeline 2
        'FEED_URI': 'reviewresult.json'                       # Used for pipeline 2
    }
    
    def parse(self, response):
        for user in response.xpath('//*[@class="sr2-review-list-container full clearfix js-sr2-review-list-container"]'):
            self.log(user,logging.WARN)
            #open_in_browswer(response)
            inspect_response(response, self)
            yield {
                # https://stackoverflow.com/questions/20081024/scrapy-get-request-url-in-parse
                'link': response.url,
                'user': user.xpath('div[1]/section/div[1]/a/text()').extract(),
                'user_url' : user.xpath('div[1]/section/div[1]/a/@href').extract(),
                'rating': user.xpath('div[2]/section/div[1]/div[1]/div').extract(),
                'taste_star_1': user.xpath('div[3]/section/div[2]/div[2]/span[1]').extract(),
                'taste_star_2': user.xpath('div[3]/section/div[2]/div[2]/span[2]').extract(),
                'taste_star_3': user.xpath('div[3]/section/div[2]/div[2]/span[3]').extract(),
                'taste_star_4': user.xpath('div[3]/section/div[2]/div[2]/span[4]').extract(),
                'taste_star_5': user.xpath('div[3]/section/div[2]/div[2]/span[5]').extract(),
                'decor_star_1': user.xpath('div[3]/section/div[3]/div[2]/span[1]').extract(),               
                'decor_star_2': user.xpath('div[3]/section/div[3]/div[2]/span[2]').extract(),              
                'decor_star_3': user.xpath('div[3]/section/div[3]/div[2]/span[3]').extract(),               
                'decor_star_4': user.xpath('div[3]/section/div[3]/div[2]/span[4]').extract(),                
                'decor_star_5': user.xpath('div[3]/section/div[3]/div[2]/span[5]').extract(),                
                'service_star_1': user.xpath('div[3]/section/div[4]/div[2]/span[1]').extract(),                                
                'service_star_2': user.xpath('div[3]/section/div[4]/div[2]/span[2]').extract(),                                
                'service_star_3': user.xpath('div[3]/section/div[4]/div[2]/span[3]').extract(),                                
                'service_star_4': user.xpath('div[3]/section/div[4]/div[2]/span[4]').extract(),                                
                'service_star_5': user.xpath('div[3]/section/div[4]/div[2]/span[5]').extract(),                                                
                'hygiene_star_1': user.xpath('div[3]/section/div[5]/div[2]/span[1]').extract(),                                                
                'hygiene_star_2': user.xpath('div[3]/section/div[5]/div[2]/span[2]').extract(),                                                
                'hygiene_star_3': user.xpath('div[3]/section/div[5]/div[2]/span[3]').extract(),                                                
                'hygiene_star_4': user.xpath('div[3]/section/div[5]/div[2]/span[4]').extract(),                                                
                'hygiene_star_5': user.xpath('div[3]/section/div[5]/div[2]/span[5]').extract(),                                                
                'value_star_1': user.xpath('div[3]/section/div[6]/div[2]/span[1]').extract(),                                                                
                'value_star_2': user.xpath('div[3]/section/div[6]/div[2]/span[2]').extract(),                                                                
                'value_star_3': user.xpath('div[3]/section/div[6]/div[2]/span[3]').extract(),                                                                
                'value_star_4': user.xpath('div[3]/section/div[6]/div[2]/span[4]').extract(),                                                                
                'value_star_5': user.xpath('div[3]/section/div[6]/div[2]/span[5]').extract(),
            }
            
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/5.0 (Windows NT 6.0; WOW64; rv:24.0) Gecko/20100101 Firefox/24.0'
})

process.crawl(ExtractSpider)
process.start()

2024-05-19 14:10:10 [scrapy.utils.log] INFO: Scrapy 2.11.2 started (bot: scrapybot)
2024-05-19 14:10:10 [scrapy.utils.log] INFO: Versions: lxml 4.8.0.0, libxml2 2.9.12, cssselect 1.2.0, parsel 1.9.1, w3lib 2.1.2, Twisted 24.3.0, Python 3.10.13 | packaged by conda-forge | (main, Dec 23 2023, 15:27:34) [MSC v.1937 64 bit (AMD64)], pyOpenSSL 24.1.0 (OpenSSL 3.2.1 30 Jan 2024), cryptography 42.0.5, Platform Windows-10-10.0.19045-SP0
2024-05-19 14:10:10 [py.warnings] WARNING: c:\Users\ahkar\.conda\envs\nlp_env\lib\site-packages\scrapy\utils\request.py:254: ScrapyDeprecationWarning:

'2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a future version of Scrapy.

See the documentation of the 'REQUEST_FINGERPRINTER_IMPLEMENTATIO

### Change review results (in json) into df
- Replace all crap strings and words (e.g. <span class="or-sprite-inline-block common_yellowstar_desktop...)
- Assign values to all ratings
- After assigning values, drop all irrelevant columns

In [ ]:
dfjson = pd.read_json('reviewresult.json')

# Get rid of list in dfjson
# https://stackoverflow.com/questions/27263805/pandas-when-cell-contents-are-lists-create-a-row-for-each-element-in-the-list
# https://chrisalbon.com/python/pandas_expand_cells_containing_lists.html
res = dfjson.copy()
for i in dfjson.columns:
    res[i] = dfjson[i].apply(pd.Series)

# Replacing strings with figures
# https://stackoverflow.com/questions/17142304/replace-string-value-in-entire-dataframe
res = res.replace(['<span class="or-sprite-inline-block common_yellowstar_desktop"></span>',
             '<span class=\"or-sprite-inline-block common_greystar_desktop\"></span>',
             '<div class=\"icon or-sprite-inline-block common_smiley_smile_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_ok_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_cry_62x60_desktop\"></div>'],[1,0,2,1,0])


# Consolidating ratings 
# https://stackoverflow.com/questions/25748683/pandas-sum-dataframe-rows-for-given-columns
df_final = res.copy()
ratings_categories =['taste','decor','service','hygiene','value']
for i in ratings_categories:
    df_final[i] = df_final[i+'_star_1'] + df_final[i+'_star_2'] + df_final[i+'_star_3'] + df_final[i+'_star_4'] + df_final[i+'_star_5']

# drop unnecessary columns
# https://stackoverflow.com/questions/13411544/delete-column-from-pandas-dataframe-using-python-del
drop_columns = []
for i in ratings_categories:
    drop_columns.append(i+'_star_1')
    drop_columns.append(i+'_star_2')
    drop_columns.append(i+'_star_3')
    drop_columns.append(i+'_star_4')
    drop_columns.append(i+'_star_5')

df_final = df_final.drop(drop_columns, axis=1)

####################################################################################################################################
# Downward fill the links
# https://stackoverflow.com/questions/27905295/how-to-replace-nans-by-preceding-values-in-pandas-dataframe
# df_final['link'] = df_final['link'].fillna(method='ffill')

# delete rows without any user_url
# https://stackoverflow.com/questions/29314033/python-pandas-dataframe-remove-empty-cells
# df_final['user_url'].replace('', np.nan, inplace=True)
# df_final.dropna(subset=['user_url'], inplace=True)

# write to final csv file
df_final.to_csv('final.csv',encoding='utf-8',index=False )

# https://stackoverflow.com/questions/32468402/how-to-explode-a-list-inside-a-dataframe-cell-into-separate-rows/32470490

### Construct a final ROBUST csv - Joining review_url.csv & final.csv
For finalest.csv, need to incorporate:
- district
- categories
- price range

In [ ]:
df_final = pd.read_csv('final.csv')
df_review = pd.read_csv('review_url.csv')

# Replace strings to have a unique restaurant link
# https://stackoverflow.com/questions/32201222/pandas-dataframe-replace-with-regex
df_final['link'] = df_final['link'].replace(['https://www.openrice.com','\?page=.*'],['',''],regex=True)

# https://stackoverflow.com/questions/20868394/changing-a-specific-column-name-in-pandas-dataframe
df_final = df_final.rename(columns = {'link':'Review URL'})

# https://stackoverflow.com/questions/25493625/vlookup-in-pandas-using-join
df_final = df_final.merge(df_review[['Review URL','Name','District','District ID','Category ID','Category Name','Price UI','Review Count','Smile','Cry','Overall Score','Bookmark Count']],on='Review URL', how='left')

df_final.to_csv('finalest.csv',encoding='utf-8',index=False)

## Add on other restaurants from other regions

### Get a new region and save them to df_addtion

In [ ]:
region = 3999

In [ ]:
# grab the entire list of restuarants for HK on openrice, only focusing on the review links
review_url = []
category_id = []
category_name = []
name = []
district = []
district_id = []
price_UI =[]
address = []
latitude = []
longitude = []
review_count = []
score_smile = []
score_cry = []
bookmark_count = []
score_overall = []

print "Scraping region {}".format(region)

for i in range(1,20):
    r = requests.get("https://www.openrice.com/api/pois?uiLang=en&uiCity=hongkong&page="+ str(i) +"&&sortBy=Default&districtId="+str(region), headers = headers)
    result = json.loads(r.text)
    if len(result['searchResult']['paginationResult']['results']) == 0:
        break
    for j in range(len(result['searchResult']['paginationResult']['results'])):
        review_url.append(result['searchResult']['paginationResult']['results'][j]['reviewUrlUI'])
        name.append(result['searchResult']['paginationResult']['results'][j]['nameUI'].encode('utf-8'))
        district.append(result['searchResult']['paginationResult']['results'][j]['district']['name'])
        district_id.append(result['searchResult']['paginationResult']['results'][j]['district']['districtId'])
        address.append(result['searchResult']['paginationResult']['results'][j]['address'])        
        price_UI.append(result['searchResult']['paginationResult']['results'][j]['priceUI'])
        latitude.append(result['searchResult']['paginationResult']['results'][j]['mapLatitude'])
        longitude.append(result['searchResult']['paginationResult']['results'][j]['mapLongitude'])
        review_count.append(result['searchResult']['paginationResult']['results'][j]['reviewCount'])
        score_smile.append(result['searchResult']['paginationResult']['results'][j]['scoreSmile'])
        score_cry.append(result['searchResult']['paginationResult']['results'][j]['scoreCry'])
        score_overall.append(result['searchResult']['paginationResult']['results'][j]['scoreOverall'])
        bookmark_count.append(result['searchResult']['paginationResult']['results'][j]['bookmarkedUserCount'])        
        
        holder_category = []
        holder_name = []
        for k in range(len(result['searchResult']['paginationResult']['results'][j]['categories'])):
            holder_category.append(result['searchResult']['paginationResult']['results'][j]['categories'][k]['categoryId'])
            holder_name.append(result['searchResult']['paginationResult']['results'][j]['categories'][k]['name'])
        category_id.append(holder_category)
        category_name.append(holder_name)
    print "Processing page " + str(i)
    i += 1

df_addition = pd.DataFrame([name,review_url,district,district_id,category_id,category_name,price_UI,address,review_count,score_smile,score_cry,score_overall,bookmark_count,latitude,longitude]).transpose()
col = ['Name','Review URL','District','District ID','Category ID','Category Name','Price UI','Address','Review Count','Smile','Cry','Overall Score','Bookmark Count','Latitude','longitude']
df_addition.columns = col

df_addition.to_csv('additional_review_url.csv',encoding='utf-8',index=False)

Scraping region 3999
Processing page 1
Processing page 2
Processing page 3
Processing page 4
Processing page 5
Processing page 6
Processing page 7
Processing page 8
Processing page 9
Processing page 10
Processing page 11
Processing page 12
Processing page 13
Processing page 14
Processing page 15
Processing page 16
Processing page 17


### Eliminate Duplicates

For "review_url.csv":
- For existing restaurants: Update Smiles, Cry, Overall Score, Bookmark Count
- Append new restaurants at the end

For "additional_reivew_url.csv":
- Update Review Count by eliminating what we had before (using New Review Count - Old Review Count)
- Prep the list of URLs to scrape

In [ ]:
df = pd.read_csv('review_url.csv')

for i in df_addition['Review URL']:
    # https://stackoverflow.com/questions/30944577/check-if-string-is-in-a-pandas-dataframe
    if df['Review URL'].str.contains(i).any():
        # https://stackoverflow.com/questions/36684013/extract-column-value-based-on-another-column-pandas-dataframe
        df.loc[df['Review URL'] == i, 'Smile'] = df_addition.loc[df_addition['Review URL'] == i, 'Smile'].iloc[0]
        df.loc[df['Review URL'] == i, 'Cry'] = df_addition.loc[df_addition['Review URL'] == i, 'Cry'].iloc[0]
        df.loc[df['Review URL'] == i, 'Overall Score'] = df_addition.loc[df_addition['Review URL'] == i, 'Overall Score'].iloc[0]
        df.loc[df['Review URL'] == i, 'Bookmark Count'] = df_addition.loc[df_addition['Review URL'] == i, 'Bookmark Count'].iloc[0]
        df_addition.loc[df_addition['Review URL'] == i, 'Review Count'] = df_addition.loc[df_addition['Review URL'] == i, 'Review Count'].iloc[0] - df.loc[df['Review URL'] == i, 'Review Count'].iloc[0]
    else:
        # https://stackoverflow.com/questions/39815646/pandas-append-dataframe-to-another-df
        df = df.append(df_addition.loc[df_addition['Review URL'] == i],ignore_index=True)

df.to_csv('review_url.csv',encoding='utf-8',index=False)
df_addition.to_csv('additional_review_url.csv',encoding='utf-8',index=False)

review_urls = []

for k in range(len(df_addition['Review Count'])):
    num_of_review_pages = math.ceil(df_addition['Review Count'][k] / 15.0)

    for i in range(1,int(num_of_review_pages)):
        review_urls.append('https://www.openrice.com'+ str(df_addition['Review URL'][k]) + '?page='+ str( i ))
# print review_urls
print "There is {} urls to scrape".format(len(review_urls))


### Scrapy for ADDITIONAL reviews for all the urls

In [ ]:
class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('additionalreviewresult.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item


class ExtractSpider(scrapy.Spider):
    name = "Extract"
    start_urls = review_urls

    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1}, # Used for pipeline 1
        'FEED_FORMAT':'json',                                 # Used for pipeline 2
        'FEED_URI': 'additionalreviewresult.json'                        # Used for pipeline 2
    }
    
    def parse(self, response):
        for user in response.xpath('//*[@class="sr2-review-list-container full clearfix js-sr2-review-list-container"]'):
            yield {
                # https://stackoverflow.com/questions/20081024/scrapy-get-request-url-in-parse
                'link': response.url,
                'user': user.xpath('div[1]/section/div[1]/a/text()').extract(),
                'user_url' : user.xpath('div[1]/section/div[1]/a/@href').extract(),
                'rating': user.xpath('div[2]/section/div[1]/div[1]/div').extract(),
                'taste_star_1': user.xpath('div[3]/section/div[2]/div[2]/span[1]').extract(),
                'taste_star_2': user.xpath('div[3]/section/div[2]/div[2]/span[2]').extract(),
                'taste_star_3': user.xpath('div[3]/section/div[2]/div[2]/span[3]').extract(),
                'taste_star_4': user.xpath('div[3]/section/div[2]/div[2]/span[4]').extract(),
                'taste_star_5': user.xpath('div[3]/section/div[2]/div[2]/span[5]').extract(),
                'decor_star_1': user.xpath('div[3]/section/div[3]/div[2]/span[1]').extract(),               
                'decor_star_2': user.xpath('div[3]/section/div[3]/div[2]/span[2]').extract(),              
                'decor_star_3': user.xpath('div[3]/section/div[3]/div[2]/span[3]').extract(),               
                'decor_star_4': user.xpath('div[3]/section/div[3]/div[2]/span[4]').extract(),                
                'decor_star_5': user.xpath('div[3]/section/div[3]/div[2]/span[5]').extract(),                
                'service_star_1': user.xpath('div[3]/section/div[4]/div[2]/span[1]').extract(),                                
                'service_star_2': user.xpath('div[3]/section/div[4]/div[2]/span[2]').extract(),                                
                'service_star_3': user.xpath('div[3]/section/div[4]/div[2]/span[3]').extract(),                                
                'service_star_4': user.xpath('div[3]/section/div[4]/div[2]/span[4]').extract(),                                
                'service_star_5': user.xpath('div[3]/section/div[4]/div[2]/span[5]').extract(),                                                
                'hygiene_star_1': user.xpath('div[3]/section/div[5]/div[2]/span[1]').extract(),                                                
                'hygiene_star_2': user.xpath('div[3]/section/div[5]/div[2]/span[2]').extract(),                                                
                'hygiene_star_3': user.xpath('div[3]/section/div[5]/div[2]/span[3]').extract(),                                                
                'hygiene_star_4': user.xpath('div[3]/section/div[5]/div[2]/span[4]').extract(),                                                
                'hygiene_star_5': user.xpath('div[3]/section/div[5]/div[2]/span[5]').extract(),                                                
                'value_star_1': user.xpath('div[3]/section/div[6]/div[2]/span[1]').extract(),                                                                
                'value_star_2': user.xpath('div[3]/section/div[6]/div[2]/span[2]').extract(),                                                                
                'value_star_3': user.xpath('div[3]/section/div[6]/div[2]/span[3]').extract(),                                                                
                'value_star_4': user.xpath('div[3]/section/div[6]/div[2]/span[4]').extract(),                                                                
                'value_star_5': user.xpath('div[3]/section/div[6]/div[2]/span[5]').extract(),
            }
            
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/5.0 (Windows NT 6.0; WOW64; rv:24.0) Gecko/20100101 Firefox/24.0'
})

process.crawl(ExtractSpider)
process.start()

### Change review results (in json) into df
- Replace all crap strings and words (e.g. <span class="or-sprite-inline-block common_yellowstar_desktop...)
- Assign values to all ratings
- After assigning values, drop all irrelevant columns

In [ ]:
dfjson = pd.read_json('additionalreviewresult.json')

# Get rid of list in dfjson
# https://stackoverflow.com/questions/27263805/pandas-when-cell-contents-are-lists-create-a-row-for-each-element-in-the-list
# https://chrisalbon.com/python/pandas_expand_cells_containing_lists.html
res = dfjson.copy()
for i in dfjson.columns:
    res[i] = dfjson[i].apply(pd.Series)

# Replacing strings with figures
# https://stackoverflow.com/questions/17142304/replace-string-value-in-entire-dataframe
res = res.replace(['<span class="or-sprite-inline-block common_yellowstar_desktop"></span>',
             '<span class=\"or-sprite-inline-block common_greystar_desktop\"></span>',
             '<div class=\"icon or-sprite-inline-block common_smiley_smile_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_ok_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_cry_62x60_desktop\"></div>'],[1,0,2,1,0])


# Consolidating ratings 
# https://stackoverflow.com/questions/25748683/pandas-sum-dataframe-rows-for-given-columns
df_final = res.copy()
ratings_categories =['taste','decor','service','hygiene','value']
for i in ratings_categories:
    df_final[i] = df_final[i+'_star_1'] + df_final[i+'_star_2'] + df_final[i+'_star_3'] + df_final[i+'_star_4'] + df_final[i+'_star_5']

# drop unnecessary columns
# https://stackoverflow.com/questions/13411544/delete-column-from-pandas-dataframe-using-python-del
drop_columns = []
for i in ratings_categories:
    drop_columns.append(i+'_star_1')
    drop_columns.append(i+'_star_2')
    drop_columns.append(i+'_star_3')
    drop_columns.append(i+'_star_4')
    drop_columns.append(i+'_star_5')

df_final = df_final.drop(drop_columns, axis=1)

####################################################################################################################################
# Downward fill the links
# https://stackoverflow.com/questions/27905295/how-to-replace-nans-by-preceding-values-in-pandas-dataframe
# df_final['link'] = df_final['link'].fillna(method='ffill')

# delete rows without any user_url
# https://stackoverflow.com/questions/29314033/python-pandas-dataframe-remove-empty-cells
# df_final['user_url'].replace('', np.nan, inplace=True)
# df_final.dropna(subset=['user_url'], inplace=True)

# write to final csv file
df_final.to_csv('additional_final.csv',encoding='utf-8',index=False )

# https://stackoverflow.com/questions/32468402/how-to-explode-a-list-inside-a-dataframe-cell-into-separate-rows/32470490

### Construct a final ROBUST csv - Joining review_url.csv & final.csv
For finalest.csv, need to incorporate:
- district
- categories
- price range

In [ ]:
df_final = pd.read_csv('additional_final.csv')
df_review = pd.read_csv('review_url.csv')
df_finalest = pd.read_csv('finalest.csv')

# Replace strings to have a unique restaurant link
# https://stackoverflow.com/questions/32201222/pandas-dataframe-replace-with-regex
df_final['link'] = df_final['link'].replace(['https://www.openrice.com','\?page=.*'],['',''],regex=True)

# https://stackoverflow.com/questions/20868394/changing-a-specific-column-name-in-pandas-dataframe
df_final = df_final.rename(columns = {'link':'Review URL'})

# https://stackoverflow.com/questions/25493625/vlookup-in-pandas-using-join
df_final = df_final.merge(df_review[['Review URL','Name','District','District ID','Category ID','Category Name','Price UI','Review Count','Smile','Cry','Overall Score','Bookmark Count']],on='Review URL', how='left')


# append to finalest
df_finalest = df_finalest.append(df_final, ignore_index = True)

df_finalest.to_csv('finalest.csv',encoding='utf-8',index=False)

# (DONT USE) User specific

## Define user id

In [ ]:
user_id = widgets.Text()
display(user_id)
# user_id = 50022270

In [ ]:
user_home_url = 'https://www.openrice.com/en/gourmet/reviews.htm?userid='+str(user_id.value)+'&reviewlang=en%2chk&page=1'

## Build user specific review URLs

In [ ]:
user_page = requests.get(user_home_url,headers=headers)

soup = BeautifulSoup(user_page.text,'html.parser')

num_of_reviews = [int(s) for s in str(soup.findAll('div',{'class':'PR15 FL'})[0].getText()).split() if s.isdigit()][2]

num_of_fans = int(filter(str.isdigit,str(soup.findAll('div',{'class':'count'})[1].getText())))

num_of_user_pages = math.ceil(num_of_reviews/10.0)

In [ ]:
user_review_urls = []
for i in range(1,int(num_of_user_pages) + 1):
    user_review_urls.append('https://www.openrice.com/en/gourmet/reviews.htm?userid='+str(user_id)+'&reviewlang=en%2chk&page='+str(i))

In [ ]:
class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('userresult.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item

In [ ]:
class ExtractSpider(scrapy.Spider):
    name = "Extract"
    start_urls = user_review_urls

    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1}, # Used for pipeline 1
        'FEED_FORMAT':'json',                                 # Used for pipeline 2
        'FEED_URI': 'userresult.json'                        # Used for pipeline 2
    }
    
    def parse(self, response):
        for user in response.xpath('//*[@class="sr2_review_title"]'):
            yield {
                'review_links':user.xpath('a/@href').extract()
            }
        

In [ ]:
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/5.0 (Windows NT 6.0; WOW64; rv:24.0) Gecko/20100101 Firefox/24.0'
})

process.crawl(ExtractSpider)
process.start()

## Scrape user's each review urls for ratings & views

In [ ]:
# read into the review links
dfjson = pd.read_json('userresult.json')

In [ ]:
user_review_url_parse = []
for i in range(len(dfjson['review_links'])):
    user_review_url_parse.append('https://www.openrice.com'+ str(dfjson['review_links'][i][0]))

In [ ]:
class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('userreviewresult.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item
    
class ExtractSpider(scrapy.Spider):
    name = "Extract"
    start_urls = user_review_url_parse

    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1}, # Used for pipeline 1
        'FEED_FORMAT':'json',                                 # Used for pipeline 2
        'FEED_URI': 'userreviewresult.json'                        # Used for pipeline 2
    }
    
    def parse(self, response):                         
        for user in response.xpath('//*[@id="global-container"]'):
            yield {
                'restaurant_link' : user.xpath('main/div[2]/div[1]/div[4]/div/ul/li[2]/a/@href').extract(),
                'district': user.xpath('main/div[2]/div[1]/div[1]/section/div[2]/div[2]/div[3]/div[1]/a/text()').extract(),
                'district_2': user.xpath('main/div[2]/div[1]/div[1]/div/section/div/div[2]/div/div[2]/div[2]/div[2]/div[1]/div[2]/div[1]/a/text()').extract(),
                'price_range': user.xpath('main/div[2]/div[1]/div[1]/section/div[2]/div[2]/div[3]/div[2]/a/text()').extract(),
                'price_range_2': user.xpath('main/div[2]/div[1]/div[1]/div/section/div/div[2]/div/div[2]/div[2]/div[2]/div[1]/div[2]/div[2]/a/text()').extract(),
                'category': user.xpath('main/div[2]/div[1]/div[1]/section/div[2]/div[2]/div[3]/div[3]').extract(),
                'category_2': user.xpath('main/div[2]/div[1]/div[1]/div/section/div/div[2]/div/div[2]/div[2]/div[2]/div[1]/div[2]/div[3]').extract(),
                # https://stackoverflow.com/questions/16843088/how-to-get-the-original-start-url-in-scrapy-before-redirect
                'link': response.request.meta['redirect_urls'][1],
                'user': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[1]/section/div[1]/a/text()').extract(),
                'user_url' : user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[1]/section/div[1]/a/@href').extract(),
                'rating': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[2]/section/div[1]/div[1]/div').extract(),
                'recommend': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[2]/section/div[1]/div[2]/div[2]/span[2]/span[2]/text()').extract(),
                'taste_star_1': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[2]/div[2]/span[1]').extract(),
                'taste_star_2': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[2]/div[2]/span[2]').extract(),
                'taste_star_3': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[2]/div[2]/span[3]').extract(),
                'taste_star_4': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[2]/div[2]/span[4]').extract(),
                'taste_star_5': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[2]/div[2]/span[5]').extract(),
                'decor_star_1': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[3]/div[2]/span[1]').extract(),               
                'decor_star_2': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[3]/div[2]/span[2]').extract(),              
                'decor_star_3': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[3]/div[2]/span[3]').extract(),               
                'decor_star_4': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[3]/div[2]/span[4]').extract(),                
                'decor_star_5': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[3]/div[2]/span[5]').extract(),                
                'service_star_1': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[4]/div[2]/span[1]').extract(),                                
                'service_star_2': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[4]/div[2]/span[2]').extract(),                                
                'service_star_3': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[4]/div[2]/span[3]').extract(),                                
                'service_star_4': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[4]/div[2]/span[4]').extract(),                                
                'service_star_5': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[4]/div[2]/span[5]').extract(),                                                
                'hygiene_star_1': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[5]/div[2]/span[1]').extract(),                                                
                'hygiene_star_2': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[5]/div[2]/span[2]').extract(),                                                
                'hygiene_star_3': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[5]/div[2]/span[3]').extract(),                                                
                'hygiene_star_4': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[5]/div[2]/span[4]').extract(),                                                
                'hygiene_star_5': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[5]/div[2]/span[5]').extract(),                                                
                'value_star_1': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[6]/div[2]/span[1]').extract(),                                                                
                'value_star_2': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[6]/div[2]/span[2]').extract(),                                                                
                'value_star_3': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[6]/div[2]/span[3]').extract(),                                                                
                'value_star_4': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[6]/div[2]/span[4]').extract(),                                                                
                'value_star_5': user.xpath('//*[@id="sr2-review-container"]/div[2]/div[1]/div[3]/section/div[6]/div[2]/span[5]').extract(),                                                                                
            }

process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/5.0 (Windows NT 6.0; WOW64; rv:24.0) Gecko/20100101 Firefox/24.0'
})

process.crawl(ExtractSpider)
process.start()

In [ ]:
dfjson = pd.read_json('userreviewresult.json')

# Getting rid of list in dfjson
# https://stackoverflow.com/questions/27263805/pandas-when-cell-contents-are-lists-create-a-row-for-each-element-in-the-list
# https://chrisalbon.com/python/pandas_expand_cells_containing_lists.html
res = dfjson.copy()
for i in dfjson.columns:
    res[i] = dfjson[i].apply(pd.Series)

# Replacing strings with figures
# https://stackoverflow.com/questions/17142304/replace-string-value-in-entire-dataframe
res = res.replace(['<span class="or-sprite-inline-block common_yellowstar_desktop"></span>',
             '<span class=\"or-sprite-inline-block common_greystar_desktop\"></span>',
             '<div class=\"icon or-sprite-inline-block common_smiley_smile_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_ok_60x60_desktop\"></div>',
            '<div class=\"icon or-sprite-inline-block common_smiley_cry_62x60_desktop\"></div>'],[1,0,2,1,0])


# Consolidating ratings 
# https://stackoverflow.com/questions/25748683/pandas-sum-dataframe-rows-for-given-columns
df_final = res.copy()
ratings_categories =['taste','decor','service','hygiene','value']
for i in ratings_categories:
    df_final[i] = df_final[i+'_star_1'] + df_final[i+'_star_2'] + df_final[i+'_star_3'] + df_final[i+'_star_4'] + df_final[i+'_star_5']

# drop unnecessary columns
# https://stackoverflow.com/questions/13411544/delete-column-from-pandas-dataframe-using-python-del
drop_columns = []
for i in ratings_categories:
    drop_columns.append(i+'_star_1')
    drop_columns.append(i+'_star_2')
    drop_columns.append(i+'_star_3')
    drop_columns.append(i+'_star_4')
    drop_columns.append(i+'_star_5')

df_final = df_final.drop(drop_columns, axis=1)

'''
# Downward fill the links
# https://stackoverflow.com/questions/27905295/how-to-replace-nans-by-preceding-values-in-pandas-dataframe
df_final['link'] = df_final['link'].fillna(method='ffill')

# delete rows without any user_url
# https://stackoverflow.com/questions/29314033/python-pandas-dataframe-remove-empty-cells
df_final['user_url'].replace('', np.nan, inplace=True)
df_final.dropna(subset=['user_url'], inplace=True)
'''
# Fill in empty Category, Price Range and district cells with previous columns
# https://stackoverflow.com/questions/38256369/fill-blank-cells-from-previous-columns-pandas-python
df_final['category_2'] = df_final['category_2'].combine_first(df_final['category'])
df_final['district_2'] = df_final['district_2'].combine_first(df_final['district'])
df_final['price_range_2'] = df_final['price_range_2'].combine_first(df_final['price_range'])

df_final = df_final.drop(['category','district','price_range'], axis=1)
# https://stackoverflow.com/questions/32468402/how-to-explode-a-list-inside-a-dataframe-cell-into-separate-rows/32470490

# write to final csv file
df_final.to_csv('userfinal.csv',encoding='utf-8',index=False )


In [ ]:
for i in range(len(df_final['category_2'])):
    soup = BeautifulSoup(df_final['category_2'][i],'html.parser')
    df_final['category_2'].loc[i] = [str(x.string) for x in soup.findAll('a')]
df_final.to_csv('userfinalest.csv',encoding='utf-8',index=False)

# Combining together

In [ ]:
user_df_final = pd.read_csv('userfinalest.csv')
review_df_final = pd.read_csv('finalest.csv')

## High-level overview of All reviews vs. User data
- Remove duplicates


Visualize in table format
- district X Price range
- Compare Category Name X Price range

In [ ]:
# https://chrisalbon.com/python/pandas_delete_duplicates.html
overview_review_df = review_df_final.drop_duplicates(['Name'], keep='last')

print "User district X price_range"
display(pd.crosstab(user_df_final['district_2'],user_df_final['price_range_2']))

print "All reviews district X price_range"
display(pd.crosstab(overview_review_df['District'],overview_review_df['Price UI']))

print "User category X price_range"
display(pd.crosstab(user_df_final['category_2'],user_df_final['price_range_2']))

print "All reviews category X price_range"
display(pd.crosstab(overview_review_df['Category Name'],overview_review_df['Price UI']))

# https://stackoverflow.com/questions/38309729/count-unique-values-with-pandas
# review_df_final.groupby('District')['Name'].nunique()

## Match user's restaurant with Master review data
- Eliminate other user's reviews that has no match in finalest.csv
- Eliminate user's review in finalest.csv as well

# Exploratory Data Analysis (EDA)

## Visualization - Overall
- Prices
- District
- Ratings
- Overall Score

In [19]:
df_restaurant_final = pd.read_csv('review_url.csv')

In [20]:
df_restaurant_final['District'].iplot(kind='hist',dimensions=(1300,500),title='Top reviewed restaurants in HK by District')

In [21]:
df_restaurant_final['Price UI'].iplot(kind='hist',dimensions=(1300,500),title='Top reviewed restaurants in HK by Price')

In [22]:
df_restaurant_final['Review Count'].iplot(kind='hist',dimensions=(1300,500),title='Top reviewed restaurants in HK by Review Count',bins=100)

In [23]:
df_restaurant_final.sort_values(['Review Count'],ascending=False).head(10)

Name  \
315  Australia Dairy Company 澳洲牛奶公司   
22              Sing Heung Yuen 勝香園   
389      Wai Kee Noodle Cafe 維記咖啡粉麵   
100         Kau Kee Restaurant 九記牛腩   
475                             EXP   
464               Kam Wah Cafe 金華冰廳   
0                         Burgeroom   
153         Lin Heung Tea House 蓮香樓   
524                  Gala Cafe 嘉樂冰廳   
358                The Greenery 雅苑座   

                                            Review URL       District  \
315  /en/hongkong/r-australia-dairy-company-jordan-...         Jordan   
22   /en/hongkong/r-sing-heung-yuen-central-hong-ko...        Central   
389  /en/hongkong/r-wai-kee-noodle-cafe-sham-shui-p...   Sham Shui Po   
100  /en/hongkong/r-kau-kee-restaurant-central-guan...        Central   
475  /en/hongkong/r-exp-kowloon-tong-western-pizza-...   Kowloon Tong   
464  /en/hongkong/r-kam-wah-cafe-prince-edward-hong...  Prince Edward   
0    /en/hongkong/r-burgeroom-causeway-bay-american...   Causeway Bay   
153  /en/hongkong/r-lin-heung-tea-house-central-gua...        Central   
524  /en/hongkong/r-gala-cafe-tsuen-wan-hong-kong-s...      Tsuen Wan   
358  /en/hongkong/r-the-greenery-tsim-sha-tsui-west...  Tsim Sha Tsui   

     District ID                              Category ID  \
315         2028                       [1004, 1014, 1009]   
22          1003                       [1004, 1009, 1016]   
389         2019                             [1004, 1010]   
100         1003                             [1002, 1010]   
475         2002                 [4000, 1022, 1021, 6000]   
464         2029                             [1004, 1009]   
0           1019                       [4001, 1035, 1007]   
153         1003  [1002, 1010, 1005, 6, 1018, 1036, 1041]   
524         3018                             [1004, 1009]   
358         2008             [4000, 1032, 1011, 12, 6000]   

                                         Category Name   Price UI  \
315         [Hong Kong Style, Dessert, Tea Restaurant]  Below $50   
22     [Hong Kong Style, Tea Restaurant, Dai Pai Dong]  Below $50   
389            [Hong Kong Style, Noodles/Rice Noodles]  Below $50   
100                  [Guangdong, Noodles/Rice Noodles]  Below $50   
475           [Western, Pizza, Yoshoku, International]   $101-200   
464                  [Hong Kong Style, Tea Restaurant]  Below $50   
0                     [American, Hamburger, Fast Food]    $51-100   
153  [Guangdong, Noodles/Rice Noodles, Dim Sum Rest...   $101-200   
524                  [Hong Kong Style, Tea Restaurant]    $51-100   
358  [Western, Buffet, Hotel Restaurant, Family Sty...   $401-800   

                                               Address  Review Count   Smile  \
315                           G/F, 47-49 Parkes Street          2574  1572.0   
22                                    2 Mei Lun Street          1292   920.0   
389  G/F, 62 & 67 Fuk Wing Street / Shop D, G/F, 16...          1023   641.0   
100                               G/F, 21 Gough Street           951   496.0   
475     Shop 23, UG, Festival Walk, 80 Tat Chee Avenue           948   637.0   
464                                G/F, 47 Bute Street           923   541.0   
0    Shop D, G/F, Food Street, 50-56 Paterson Stree...           846   684.0   
153                          160-164 Wellington Street           791   503.0   
524                          G/F, 40B San Chuen Street           751   418.0   
358                3/F, The Royal Garden, 69 Mody Road           750   497.0   

       Cry  Overall Score  Bookmark Count   Latitude   longitude  
315  267.0       3.501682           33429  22.304584  114.170592  
22    76.0       3.525467           35916  22.284118  114.152536  
389   88.0       3.374304           14972  22.331499  114.163477  
100  173.0       3.219213           29829  22.284272  114.152648  
475   53.0       3.633481            6073  22.337302  114.174672  
464   96.0       3.405843           20093  22.322309  114.169761  
0     47.0     

In [24]:
df_restaurant_final['Overall Score'].iplot(kind='hist',dimensions=(1300,500),title='Top reviewed restaurants in HK by Overall Score')

In [25]:
df_restaurant_final.sort_values(['Overall Score'],ascending=True).head(10)

Name  \
688                     Kei Kee Dessert 佳記甜品   
693                 Yue Kee Restaurant 裕記大飯店   
683  Yunnan Guizhou & Sichuan Noodle 唯一雲貴川風味   
410                          Scoool Cafe 小時光   
561                     Kei Kee Dessert 佳記甜品   
100                  Kau Kee Restaurant 九記牛腩   
383                         Big Bang Don 爆丼屋   
680                              Fooody 伙食工業   
524                           Gala Cafe 嘉樂冰廳   
186                     Wing Kee Noodle 榮記粉麵   

                                            Review URL      District  \
688  /en/hongkong/r-kei-kee-dessert-yuen-long-hong-...     Yuen Long   
693  /en/hongkong/r-yue-kee-restaurant-sham-tseng-g...    Sham Tseng   
683  /en/hongkong/r-yunnan-guizhou-sichuan-noodle-t...     Tsuen Wan   
410  /en/hongkong/r-scoool-cafe-kwun-tong-taiwan-r4...     Kwun Tong   
561  /en/hongkong/r-kei-kee-dessert-yuen-long-hong-...     Yuen Long   
100  /en/hongkong/r-kau-kee-restaurant-central-guan...       Central   
383  /en/hongkong/r-big-bang-don-mong-kok-japanese-...      Mong Kok   
680  /en/hongkong/r-fooody-fo-tan-hong-kong-style-a...        Fo Tan   
524  /en/hongkong/r-gala-cafe-tsuen-wan-hong-kong-s...     Tsuen Wan   
186  /en/hongkong/r-wing-kee-noodle-causeway-bay-ho...  Causeway Bay   

     District ID                           Category ID  \
688         3003                          [1004, 1014]   
693         3010                 [1002, 1020, 1001, 5]   
683         3018                          [1003, 1010]   
410         2026                    [1009, 1008, 1024]   
561         3003                    [1004, 1014, 1202]   
100         1003                          [1002, 1010]   
383         2010                          [2009, 1034]   
680         3013  [1004, 1005, 1008, 1009, 1036, 1075]   
524         3018                          [1004, 1009]   
186         1019                    [1004, 1004, 1010]   

                                         Category Name   Price UI  \
688                         [Hong Kong Style, Dessert]  Below $50   
693  [Guangdong, Chinese BBQ, Stir-Fry, Drivers Fri...   $101-200   
683                     [Yunnan, Noodles/Rice Noodles]  Below $50   
410            [Taiwan, Coffee Shop, Upper-floor Cafe]    $51-100   
561             [Hong Kong Style, Dessert, Sweet Soup]  Below $50   
100                  [Guangdong, Noodles/Rice Noodles]  Below $50   
383                          [Japanese, Sushi/Sashimi]   $101-200   
680  [Hong Kong Style, Ramen, Coffee Shop, Taiwan, ...    $51-100   
524                  [Hong Kong Style, Tea Restaurant]    $51-100   
186  [Hong Kong Style, Food Stall Noodles, Noodles/...  Below $50   

                                               Address  Review Count  Smile  \
688                                      Kau Yuk Road,           505  168.0   
693                              G/F, 9 Sham Hong Road           285  135.0   
683                             G/F, 14 Sze Pei Square           334  156.0   
410  Flat C, 1/F, Mai Hing Industrial Building Bloc...           320  115.0   
561                              Shop 7, Chi Fu Centre           390  185.0   
100                               G/F, 21 Gough Street           951  496.0   
383                         Shop 8, G/F, 50 Soy Street           341  140.0   
680  Shop No. 3, G/F, Leader Industrial Centre, 57-...           136   52.0   
524                          G/F, 40B San Chuen Street           751  418.0   
186                              G/F, 27A Sugar Street           318  180.0   

       Cry  Overall Score  Bookmark Count   Latitude   longitude  
688  137.0       2.828448            1822  22.442650  114.025984  
693   71.0       3.089259            2677  22.369104  114.059445  
683   56.0       3.126897            5349  22.369662  114.117506  
410   49.0       3.139261           19368  22.308749  114.225032  
561   42.0       3.189566            4250  22.442232  114.030962  
100  173.0       3.219213           29829  22.2

In [26]:
df_restaurant_final['Category Name'].iplot(kind='hist',dimensions=(1300,500),title='Top reviewed restaurants in HK by Overall Score')

In [ ]:
df_restaurant_final[['District','Price UI','Smile','Cry','Review Count','Bookmark Count','Overall Score','Category Name']].iplot(kind='hist', subplots=True,  dimensions=(1300,1500))

## Visualization - User specific (Use 'finalest.csv')

In [ ]:
# user_df_final = pd.read_csv('userfinalest.csv')
review_df_final = pd.read_csv('finalest.csv')
# Drop any row with empty cells
df_finalest = review_df_final.dropna()
# calculate total score
df_finalest['final score'] = df_finalest[['rating','taste','decor','service','hygiene','value']].sum(axis=1)

In [ ]:
df_finalest['District'].iplot(kind='hist',dimensions=(1300,500),title='Users Overall by District')

In [ ]:
df_finalest['final score'].iplot(kind='hist',dimensions=(1300,500),title='Users Overall Score')

In [ ]:
df_finalest[['District','Price UI','final score','rating','taste','decor','service','hygiene','value','Category Name']].iplot(kind='hist', subplots=True,  dimensions=(1300,1500))

# Recommendation Model

## Model

Reference: 
- [Matrix Factorization for Movie Recommendations in Python](https://beckernick.github.io/matrix-factorization-recommender/)
- [[Using Surprise] - The easy guide for building python collaborative filtering recommendation system in 2017](https://medium.com/@m_n_malaeb/the-easy-guide-for-building-python-collaborative-filtering-recommendation-system-in-2017-d2736d2e92a8)
- [Implementing your own recommender systems in Python](https://cambridgespark.com/content/tutorials/implementing-your-own-recommender-systems-in-Python/index.html)
- [Netflix version - simpler](https://nikhilwins.wordpress.com/2015/09/18/movie-recommendations-how-does-netflix-do-it-a-9-step-coding-intuitive-guide-into-collaborative-filtering/)

$~$

Learning Videos:

- [Matrix Factorization and Advanced Techniques - Singular Value Decomposition](https://www.coursera.org/learn/matrix-factorization/lecture/K5NBy/singular-value-decomposition)

### Training & Testing set

$~$

- Locate the users that reviewed > 10 times (from finalest.csv)
- Take out 10% of what they have reviewed

$~$


In [27]:
# user_df_final = pd.read_csv('userfinalest.csv')
df_finalest = pd.read_csv('finalest.csv')
# Drop any row with empty cells
df_finalest = df_finalest.dropna()
# calculate total score
df_finalest['final score'] = df_finalest[['rating','taste','decor','service','hygiene','value']].sum(axis=1)

# Drop irrelevant data
df_finalest = df_finalest.drop(['District','District ID','Category ID','Category Name','Price UI','Review Count','Smile','Cry','Overall Score','Bookmark Count'], axis=1)

In [29]:
# Show which users have the most reviews
most_reviews_users_df = df_finalest['Name'].groupby(df_finalest["user"]).count().sort_values(ascending=False)

top_users = most_reviews_users_df.index[0:51].tolist()
# most_reviews_users_df[0:50].sum()

In [30]:
# choose 10% sample from the top user and remove -> for testing purpose
top_user_test = df_finalest[df_finalest['user'].isin(top_users)].sample( int(math.floor(float(most_reviews_users_df[0:51].sum())*0.1)) )
print 'Before: ' + str(len(df_finalest))

df_finalest = df_finalest.drop(top_user_test.index)
print 'After: ' + str(len(df_finalest))

print 'User with most reviews in this dataset is ' + str(most_reviews_users_df.index[0])

Before: 151162
After: 149971
User with most reviews in this dataset is mandymanlovefoodie


### Model building & Running

In [31]:
R_df = pd.pivot_table(df_finalest,values = 'final score',index = 'user',columns = 'Name').fillna(0)
R_df.head()

Name           101 Grill Bar + Hot Pot 101手工涮涮鍋  101手工涮涮鍋  16 Shell  \
user                                                                  
 Little Rainy                               0.0       0.0      19.0   
 reeseang                                   0.0       0.0       0.0   
 susanso5215                                0.0       0.0       0.0   
 安格斯娘                                       0.0       0.0       0.0   
!PUMPS!                                     0.0       0.0       0.0   

Name           18樓雞煲火鍋專門店  1963 木十豆寸  2+2 Café  616牛肉火鍋專門店  66 Hot Pot 陸陸雞煲火鍋  \
user                                                                            
 Little Rainy         0.0        0.0       0.0         0.0                0.0   
 reeseang             0.0        0.0       0.0         0.0                0.0   
 susanso5215          0.0        0.0       0.0         0.0                0.0   
 安格斯娘                 0.0        0.0       0.0         0.0                0.0   
!PUMPS!               0.0        0.0       0.0         0.0                0.0   

Name           8鍋臭臭鍋  A La Umai      ...       鍋心粥底火鍋  隱世貳館   韓舍  餃子屋  \
user                                 ...                                
 Little Rainy    0.0        0.0      ...          0.0   0.0  0.0  0.0   
 reeseang        0.0        0.0      ...          0.0   0.0  0.0  0.0   
 susanso5215     0.0        0.0      ...          0.0   0.0  0.0  0.0   
 安格斯娘            0.0        0.0      ...          0.0   0.0  0.0  0.0   
!PUMPS!          0.0        0.0      ...          0.0   0.0  0.0  0.0   

Name           養心殿台式養生鍋  馬辣台式鴛鴦火鍋  鳴橋燒肉料理  麻痺雞  麻辣串串香  龍門一番 上海·紫砂燉湯  
user                                                                 
 Little Rainy       0.0       0.0     0.0  0.0    0.0           0.0  
 reeseang           0.0       0.0     0.0  0.0    0.0           0.0  
 susanso5215        0.0       0.0     0.0  0.0    0.0           0.0  
 安格斯娘               0.0       0.0     0.0  0.0    0.0           0.0  
!PUMPS!             0.0       0.0     0.0  0.0    0.0           0.0  

[5 rows x 667 columns]

In [32]:
sparsity=round(1.0-len(R_df)/float(len(R_df.index)*len(R_df.columns)),3)
print 'The sparsity level of Openrice is ' +  str(sparsity*100) + '%'

The sparsity level of Openrice is 99.9%


In [33]:
R = R_df.as_matrix()
user_ratings_mean = np.mean(R, axis = 1)
R_demeaned = R - user_ratings_mean.reshape(-1, 1)
# pd.DataFrame(R_demeaned)

In [48]:
U, sigma, Vt = svds(R_demeaned, k = 100)

In [49]:
sigma = np.diag(sigma)

In [50]:
all_user_predicted_ratings = np.dot(np.dot(U, sigma), Vt) + user_ratings_mean.reshape(-1, 1)
# np.dot(np.dot(U, sigma), Vt)

In [51]:
preds_df = pd.DataFrame(all_user_predicted_ratings, columns = R_df.columns,index = R_df.index)
# preds_df.to_csv('model-estimation.csv',encoding='utf-8')

In [52]:
def rmse(prediction, ground_truth):
    prediction = prediction[ground_truth.nonzero()].flatten()
    ground_truth = ground_truth[ground_truth.nonzero()].flatten()
    return math.sqrt(mean_squared_error(prediction, ground_truth))

### Predictions

In [73]:
def recommend_restaurants(preds_df, users, restaurants_df, original_ratings_df, num_recommendations=5,**kwargs):
    
    all_user_full = pd.DataFrame()
    all_recommendations = pd.DataFrame()
    
    for user in users:
        # Get and sort the user's predictions
        sorted_user_predictions = preds_df.loc[user].sort_values(ascending=False) 

        # Get the user's data and merge in the movie information.
        user_data = original_ratings_df[original_ratings_df.user == (user)]
    
    
        user_full = (user_data.merge(restaurants_df, how = 'left', left_on = 'Name', right_on = 'Name'))

        top_x_district = user_full.groupby(user_full['District'])['District'].count().sort_values(ascending=False)


        user_full['Category Name'].fillna('None', inplace=True)

        user_all_category = []

        for i in range(0,len(user_full['Category Name'].tolist())):
            for k in user_full['Category Name'].tolist()[i].replace("[", "").replace("]","").split(','):
                user_all_category.append(k)

        count = Counter(user_all_category)
        top_x_category = pd.DataFrame(count.items(),columns = ['Category','Count'])
        top_x_category = top_x_category.sort_values(['Count'],ascending= False)

        print 'User {0} has already rated {1} restaurantes.'.format(user, user_full.shape[0])
        print ''
        print 'Recommending highest {0} predicted ratings restaurants not already rated.'.format(num_recommendations)
        print ''
        print 'The top {0} region(s) {1} go are: {2}'.format(math.ceil(len(top_x_district)*0.1),user,top_x_district[0:int(math.ceil(len(top_x_district)*0.1))])
        print ''
        print 'The top {0} categories {1} eat are: {2}'.format(int(math.ceil(len(top_x_category)*0.25)),user,top_x_category['Category'][0:int(math.ceil(len(top_x_category)*0.25))])

        # Recommend the highest predicted rating restaurants that the user hasn't eaten yet.
        recommendations = (restaurants_df[~restaurants_df['Name'].isin(user_full['Name'])].
             merge(pd.DataFrame(sorted_user_predictions).reset_index(), how = 'left', left_on = 'Name', right_on = 'Name').
             rename(columns = {user: 'Predictions'}).
             sort_values('Predictions', ascending = False).
                           iloc[:num_recommendations, :-1]
                          )

        # Adjusting scores by District preferences, appearing in top 10%, add more points. If doesn't appear, decrease points
        j = 0
        for i in recommendations['District'][0:num_recommendations]:
            if i in top_x_district[0:int(math.ceil(len(top_x_district)*0.1))].index.tolist():
                sorted_user_predictions.loc[recommendations.iloc[j]['Name']] = sorted_user_predictions.loc[recommendations.iloc[j]['Name']] + 50
            else:
                sorted_user_predictions.loc[recommendations.iloc[j]['Name']] = sorted_user_predictions.loc[recommendations.iloc[j]['Name']] - 50      
            j += 1

        j = 0

        # Adjusting scores for Categories
        for i in recommendations['Category Name'][0:num_recommendations]:
            for k in i.replace("[", "").replace("]","").split(','):
                if k in top_x_category['Category'][0:int(math.ceil(len(top_x_category)*0.25))].tolist():
                    sorted_user_predictions.loc[recommendations.iloc[j]['Name']] = sorted_user_predictions.loc[recommendations.iloc[j]['Name']] + 50
                else:
                    sorted_user_predictions.loc[recommendations.iloc[j]['Name']] = sorted_user_predictions.loc[recommendations.iloc[j]['Name']] - 50
            j += 1

        recommendations = (restaurants_df[~restaurants_df['Name'].isin(user_full['Name'])].
             merge(pd.DataFrame(sorted_user_predictions).reset_index(), how = 'left', left_on = 'Name', right_on = 'Name').
             rename(columns = {user: 'Predictions'}).
             sort_values('Predictions', ascending = False).
                           iloc[:num_recommendations, :-1]
                          )        
        all_user_full = all_user_full.append(user_full)
        all_recommendations = all_recommendations.append(recommendations)
        
    return all_user_full, all_recommendations

In [75]:
already_rated, predictions = recommend_restaurants(preds_df, most_reviews_users_df.index[0:51], df_restaurant_final, df_finalest,num_recommendations=30)

User mandymanlovefoodie has already rated 464 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 4.0 region(s) mandymanlovefoodie go are: District
Causeway Bay     114
Mong Kok          62
Tsim Sha Tsui     59
Wan Chai          31
Name: District, dtype: int64

The top 26 categories mandymanlovefoodie eat are: 96                 Japanese
47                  Dessert
46              Coffee Shop
6                   Western
50                   Korean
54                  Seafood
22                 Stir-Fry
3           Hong Kong Style
44                Guangdong
64                  Hot Pot
94            International
86                   Skewer
27       Western Restaurant
78        All Day Breakfast
15                  Italian
34                    Ramen
88                  Dim Sum
79     Korean Fried Chicken
76               Roast Meat
56         Ice Cream/yogurt
37            Sushi/Sashimi
53                      Bar
70     Noodles/Rice Noodles

User yemenikwan has already rated 322 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 4.0 region(s) yemenikwan go are: District
Causeway Bay     64
Tsim Sha Tsui    57
Mong Kok         45
Tsuen Wan        43
Name: District, dtype: int64

The top 25 categories yemenikwan eat are: 96                 Japanese
43              Coffee Shop
6                   Western
44                  Dessert
52                  Seafood
48                   Korean
4           Hong Kong Style
63                  Hot Pot
8                   Italian
27       Western Restaurant
86                   Skewer
41            International
95          All-you-can-eat
22                 Stir-Fry
76        All Day Breakfast
42                Guangdong
51                      Bar
37            Sushi/Sashimi
25                  Western
74               Roast Meat
34                    Ramen
69     Noodles/Rice Noodles
24            International
75          Chicken Hot Pot

User sky_0721 has already rated 299 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 3.0 region(s) sky_0721 go are: District
Causeway Bay     65
Tsim Sha Tsui    61
Mong Kok         30
Name: District, dtype: int64

The top 22 categories sky_0721 eat are: 47                Seafood
82               Japanese
3         Hong Kong Style
39                Dessert
38            Coffee Shop
74                 Skewer
6                 Western
17         Tea Restaurant
80          International
85                Spanish
42                 Korean
48     Food Wise Eateries
14                Italian
23     Western Restaurant
81        All-you-can-eat
67      All Day Breakfast
32          Sushi/Sashimi
21                Western
27                   Thai
65             Roast Meat
28                  Ramen
46                    Bar
Name: Category, dtype: object
User JJcaptain has already rated 264 restaurantes.

Recommending highest 30 predicted ratings r

User yomid has already rated 278 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 3.0 region(s) yomid go are: District
Causeway Bay     60
Mong Kok         43
Tsim Sha Tsui    42
Name: District, dtype: int64

The top 21 categories yomid eat are: 20                   Korean
71                 Japanese
5                   Dessert
38                  Western
3               Coffee Shop
26                  Seafood
56                   Skewer
10     Korean Fried Chicken
65                  Hot Pot
33          Hong Kong Style
75               Roast Meat
79            International
15        All Day Breakfast
61            Sushi/Sashimi
67          All-you-can-eat
64                  Italian
31         Ice Cream/yogurt
35               Korean BBQ
43                    Ramen
42                     Thai
77                  Spanish
Name: Category, dtype: object
User Joanna H has already rated 261 restaurantes.

Recommending highest 30 predicted rat

User KaKa522 has already rated 225 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 3.0 region(s) KaKa522 go are: District
Causeway Bay     60
Tsim Sha Tsui    43
Mong Kok         20
Name: District, dtype: int64

The top 24 categories KaKa522 eat are: 89                 Japanese
21                 Stir-Fry
41                Guangdong
52                  Seafood
43                  Dessert
5                   Western
40            International
34            Sushi/Sashimi
47                   Korean
42              Coffee Shop
63                  Hot Pot
25       Western Restaurant
64                 Shanghai
16             Chinese Buns
83                  Dim Sum
81                   Skewer
92                  Spanish
26         Upper-floor Cafe
75     Korean Fried Chicken
88          All-you-can-eat
1                   Izakaya
51                      Bar
49          Hong Kong Style
85            Private Party
Name: Category, dtype: objec

User popcorn55 has already rated 236 restaurantes.

Recommending highest 30 predicted ratings restaurants not already rated.

The top 3.0 region(s) popcorn55 go are: District
Tsim Sha Tsui    50
Causeway Bay     42
Mong Kok         28
Name: District, dtype: int64

The top 20 categories popcorn55 eat are: 1               Coffee Shop
3                   Dessert
73            International
23                  Seafood
18                   Korean
35                  Western
67                 Japanese
71                  Spanish
21         Upper-floor Cafe
8      Korean Fried Chicken
20       Western Restaurant
58                  Italian
37                   Skewer
69               Roast Meat
2           Hong Kong Style
22                      Bar
13        All Day Breakfast
39                     Thai
62          All-you-can-eat
59                  Hot Pot
Name: Category, dtype: object
User mantung88 has already rated 201 restaurantes.

Recommending highest 30 predicted ratings restaurant

In [77]:
len(top_user_test)

1191

In [64]:
predictions['Name']

26                   Bilibala Yakitori Bar
224                       Dalin Pocha 達人包車
234                    Supreme Hot Pot 靚煲皇
212          Korean Inn Restaurant 高麗軒韓國料理
293                                相撲手日式放題
189                          Yadllie Plate
231        Sushi Ma Japanese Restaurant 鮨真
3             Tai Pai Tong Hong Kong 西餐大排檔
203                         Let's Jam 一起果醬
194    Aidan Korean Dessert Cafe 小火焰韓式咖啡餐廳
111                                KS Cafe
12                          Tararan-ya 鱈卵屋
183                                    壹火鍋
187                                LM Cafe
190                     Samurai Ramen 武士拉麵
120                              Le Marron
49                              Yum Cha 飲茶
214                             Yum Cha 飲茶
427                                GOCHISO
162                  FRITES Belgium on Tap
64                   FRITES Belgium on Tap
323                                 Chalet
324                       Ramen Taifu 拉麵台風
140        

In [80]:
df_predict = pd.merge(top_user_test, predictions,on='Name',how='inner')
df_predict['combine'] = df_predict['user'] + df_predict['Name']
df_predict = df_predict.drop_duplicates('combine')
len(df_predict)

842

In [29]:
df_finalest.loc[df_finalest['user']=='mandymanlovefoodie']['District'].iplot(kind='hist',dimensions=(1300,500),title='mandymanlovefoodie')

In [36]:
df_finalest.loc[df_finalest['user']=='mandymanlovefoodie'].groupby(df_finalest['District'])['District'].count().sort_values(ascending=False)

District
Causeway Bay        109
Mong Kok             62
Tsim Sha Tsui        39
Wan Chai             24
Sheung Wan           17
Central              17
Western District     15
Tsuen Wan            12
Sham Shui Po         11
Prince Edward         9
Jordan                8
Kwun Tong             7
North Point           6
Kowloon City          5
Yuen Long             5
Tai Hang              5
Tin Hau               5
Tai Wai               4
Tseung Kwan O         4
Shau Kei Wan          4
Tai Po                3
Cheung Sha Wan        3
Sha Tin               2
Tai Koo               2
Kwai Fong             2
Hung Hom              2
Yau Tong              1
Sai Wan Ho            1
Ma On Shan            1
Tsing Yi              1
Yau Ma Tei            1
Name: District, dtype: int64

In [143]:
math.ceil(len(already_rated.groupby(already_rated['District'])['District'].count().sort_values(ascending=False))*0.1)

3.0

# Using Surprise library

In [10]:
# Load the movielens-100k dataset (download it if needed),
reader = Reader(rating_scale=(1.,27.))

data = Dataset.load_from_df(df_finalest[['user_url','Review URL','final score']],reader)

# Split the dataset into 5 folds and choose the algorithm
data.split(n_folds=5)
algo = SVD()

# # Train and test reporting the RMSE and MAE scores
evaluate(algo, data, measures=['RMSE', 'MAE'])


Evaluating RMSE, MAE of algorithm SVD.

------------
Fold 1
RMSE: 3.3948
MAE:  2.4446
------------
Fold 2
RMSE: 3.3651
MAE:  2.4321
------------
Fold 3
RMSE: 3.4067
MAE:  2.4516
------------
Fold 4
RMSE: 3.3853
MAE:  2.4252
------------
Fold 5
RMSE: 3.3903
MAE:  2.4397
------------
------------
Mean RMSE: 3.3885
Mean MAE : 2.4386
------------
------------


CaseInsensitiveDefaultDict(list,
                           {'mae': [2.4446469721569475,
                             2.4320516475322083,
                             2.4515891754868795,
                             2.4251589422659756,
                             2.439705187246453],
                            'rmse': [3.3947534555815304,
                             3.3651477074326248,
                             3.4066947390478872,
                             3.3853435731345058,
                             3.3903263925512785]})

In [27]:
# Retrieve the trainset.
trainset = data.build_full_trainset()
algo.train(trainset)

# Predict a certain item
user_url = '/en/restaurant/userinfo.htm?userid=58329297'
Review_url = '/en/hongkong/r-%E7%BE%8E%E5%91%B3%E9%A4%83%E5%AD%90%E5%BA%97-prince-edward-hong-kong-style-noodles-rice-noodles-r193798/reviews'
final_score = 18
print(algo.predict(user_url, Review_url, final_score))
# print algo.predict('Alice','Titanic')

user: /en/restaurant/userinfo.htm?userid=58329297 item: /en/hongkong/r-%E7%BE%8E%E5%91%B3%E9%A4%83%E5%AD%90%E5%BA%97-prince-edward-hong-kong-style-noodles-rice-noodles-r193798/reviews r_ui = 18.00   est = 21.15   {u'was_impossible': False}


CoClustering = 22.37, RMSE = 3.5078 (FAST!)

SVD          = 21.86, RMSE = 3.3917 (FAST too!)

SVDpp        (BAD Error, manually stopped)

In [11]:
df_finalest.loc[df_finalest['user']=='mandymanlovefoodie']['final score'].iplot(kind='hist',dimensions=(1300,500),title='mandymanlovefoodie')

In [26]:
df_finalest.loc[df_finalest['user']=='mandymanlovefoodie']['Review URL'][127815]

'/en/hongkong/r-%E7%BE%8E%E5%91%B3%E9%A4%83%E5%AD%90%E5%BA%97-prince-edward-hong-kong-style-noodles-rice-noodles-r193798/reviews'

In [25]:
df_finalest.loc[df_finalest['user']=='mandymanlovefoodie']

Review URL  rating  \
2635    /en/hongkong/r-the-captains-house-tsim-sha-tsu...     2.0   
3053    /en/hongkong/r-the-grill-room-causeway-bay-wes...     2.0   
3335    /en/hongkong/r-the-grill-room-causeway-bay-wes...     2.0   
3580    /en/hongkong/r-%E4%B8%83%E7%A6%8F%E7%A5%9E%E5%...     2.0   
3761    /en/hongkong/r-%E4%B8%83%E7%A6%8F%E7%A5%9E%E5%...     2.0   
3833    /en/hongkong/r-%E4%B8%83%E7%A6%8F%E7%A5%9E%E5%...     2.0   
4249    /en/hongkong/r-goobne-chicken-tsim-sha-tsui-ko...     2.0   
4352    /en/hongkong/r-goobne-chicken-tsim-sha-tsui-ko...     2.0   
4471    /en/hongkong/r-burger-joys-wan-chai-american-h...     2.0   
4508    /en/hongkong/r-burger-joys-wan-chai-american-h...     2.0   
4603    /en/hongkong/r-burger-joys-wan-chai-american-h...     2.0   
4690    /en/hongkong/r-burger-joys-wan-chai-american-h...     2.0   
6414    /en/hongkong/r-sodam-chicken-causeway-bay-kore...     2.0   
6638    /en/hongkong/r-sodam-chicken-causeway-bay-kore...     2.0   
6870    /en/hongkong/r-toretore-hamayaki-causeway-bay-...     2.0   
6925    /en/hongkong/r-toretore-hamayaki-causeway-bay-...     2.0   
7849    /en/hongkong/r-the-pudding-nouveau-tai-hang-we...     2.0   
8259    /en/hongkong/r-hesheeat-causeway-bay-western-a...     2.0   
8329    /en/hongkong/r-hesheeat-causeway-bay-western-a...     2.0   
8828    /en/hongkong/r-thai-chef-thais-restaurant-mong...     2.0   
9037    /en/hongkong/r-thai-chef-thais-restaurant-mong...     2.0   
9238    /en/hongkong/r-mackie-kitchen-causeway-bay-wes...     2.0   
9253    /en/hongkong/r-mackie-kitchen-causeway-bay-wes...     2.0   
9286    /en/hongkong/r-mackie-kitchen-causeway-bay-wes...     2.0   
9619    /en/hongkong/r-little-vegas-causeway-bay-weste...     2.0   
10040   /en/hongkong/r-market-hotpot-mong-kok-guangdon...     2.0   
10765   /en/hongkong/r-tai-pai-tong-hong-kong-causeway...     2.0   
11608   /en/hongkong/r-shika-teppan-yaki-causeway-bay-...     2.0   
12132   /en/hongkong/r-sky726-mong-kok-international-d...     2.0   
12452   /en/hongkong/r-sushi-man-yuen-long-japanese-om...     2.0   
...                                                   ...     ...   
125006  /en/hongkong/r-meokbang-korean-bbq-bar-prince-...     2.0   
126692  /en/hongkong/r-cafe-hillywood-tsim-sha-tsui-it...     2.0   
126808  /en/hongkong/r-%E9%B3%B4%E6%A9%8B%E7%87%92%E8%...     2.0   
127296  /en/hongkong/r-daiichi-hotpot-tsim-sha-tsui-ho...     2.0   
127815  /en/hongkong/r-%E7%BE%8E%E5%91%B3%E9%A4%83%E5%...     2.0   
129351  /en/hongkong/r-romanne-leisure-food-concept-mo...     2.0   
129410  /en/hongkong/r-seafood-port-restaurant-prince-...     2.0   
132159  /en/hongkong/r-ramen-taifu-tsuen-wan-japanese-...     2.0   
132375  /en/hongkong/r-captain-restaurant-yuen-long-in...     2.0   
134620  /en/hongkong/r-shilin-taiwan-shop-yuen-long-ta...     2.0   
136060  /en/hongkong/r-whitehead-barbecue-ma-on-shan-h...     2.0   
137154  /en/hongkong/r-optimal-taste-kwai-fong-hong-ko...     2.0   
138733  /en/hongkong/r-das-bier-tai-po-german-r105135/...     2.0   
138916  /en/hongkong/r-m3-italian-tai-wai-italian-seaf...     2.0   
138924  /en/hongkong/r-m3-italian-tai-wai-italian-seaf...     2.0   
139120  /en/hongkong/r-uchi-coffee-tai-wai-japanese-de...     2.0   
141132  /en/hongkong/r-inahachi-shabu-shabu-tsuen-wan-...     2.0   
144892  /en/hongkong/r-shanxi-knife-cut-noodle-king-ts...     2.0   
151852  /en/hongkong/r-cafe-ancient-tai-wai-western-al...     2.0   
151985  /en/hongkong/r-smart-rice-noodles-kwai-fong-si...     2.0   
155385  /en/hongkong/r-tom-yum-tom-yum-tseung-kwan-o-t...     2.0   
155479  /en/hongkong/r-tom-yum-tom-yum-tseung-kwan-o-t...     1.0   
156266  /en/hongkong/r-%E5%86%AC%E8%94%AD%E5%85%AC%E5%...     2.0   
157395  /en/hongkong/r-cong-sao-star-dessert-tseung-kw...     2.0   
158154  /en/hongkong/r-%E6%BD%AE%E7%A6%8F%E8%92%B8%E6%...     2.0   
158476  /en/hongkong/r-%E9%87%8E%E5%B7%9D%E6%8B%89%E9%...     2.0   
159046  /en/hongkong/r-shu-restaurant-tsuen-w